# Riot API 

This analysis isn't endorsed by Riot Games and doesn't reflect the views or opinions of Riot Games or anyone officially involved in producing or managing Riot Games properties. Riot Games, and all associated properties are trademarks or registered trademarks of Riot Games, Inc.

REMINDER: API changes every couple of days, each hash changes along with it!

## To Do

1. (Current) Code experimentation
2. Running Collection for Dataset
3. Preparing Analysis

Priority
* Scheduling running of the collection code

* SQL Alchemy 
    * Check if tables exist, if not then create the tables
    * Duplicate handling
    * Logging just to see what's happening
    * https://docs.sqlalchemy.org/en/14/core/engines.html#dbengine-logging
    * Sessions/Transactions?
        * https://www.michaelcho.me/article/sqlalchemy-commit-flush-expire-refresh-merge-whats-the-difference
        * https://docs.sqlalchemy.org/en/14/orm/session_basics.html#session-faq-whentocreate

* Environment Preparation (Isolating just the necessary libraries to run this code
    * Is there a Better way of showing the needed libaries?

* Workflow for analysis
    * Generic
        * Match ID
            * Username
                * Ranking
    * Targeted
        * Username
           * Match information of previous matches

## Goal

Showcase DataScience with limited Data

## Plan

1. API ingestion into clear columns
1. Database Setup
    1. Users (puuid, summonerid, username)
    1. Ranking Table (summoner revision date, rank, title, lp)
1. Database insertion of data
    1. How to cache this data for the future
1. Explaining more about Team Fight Tactics


## Ideas:
* 

## Links
* https://developer.riotgames.com/apis

* https://requests.readthedocs.io/en/latest/user/quickstart/


## Lessons Learned
* Python Requests .json() returns a dict that can be encoded to JSON (AKA deserialization) requires serialization to turn into proper JSON. Difference is that the deserialization creates a dictionary that uses single quotes. However JSON requires double quotes for strings! Can use json library function dumps to serialize, or just replace single quotations with double quotations. 

* SQL Alchemy 
    * Object Oriented Programming
    * Sessions and transactions for logging purposes
    * Mostly flexible backend. There are some backend specific functions that is not universal

* Github
    * Hiding API keys through gitignore

* Rate Limiting
    * Decorator Factories (Merging Decorators)
    
* Decision on Class Creation
    * Not everything deserves to be a class
    * In my own words: "Classes are best used as interfaces where interactivity of an object is the main goal"
    * For this project the data is just being pipelined to another part, theres no altering of a single object, they're being turned into a different object
    
    
    

# Classes 
classes for more structured code? Probably best for showcasing and the API Limter decorator
For best usage Requires more than 1 method....


objects & methods
* user
    * username
    * PUUID
    


* match

* user ranking information




* Requests from the API
    * Request "account info" given username
    * Request ranking information given summoner id (https://developer.riotgames.com/apis#tft-summoner-v1)
    * Request ranking information given rank and placement (https://developer.riotgames.com/apis#tft-league-v1)
        * Top 100 Challenger
        * Top 200 GM
        * Top 100 Master
        * Per Rank and Placement (Diamond-Bronze)
    * Request Match IDs given puuid and n latest matches
    * Request Match Information given Match IDs
    
* Inserts to the Database
    * Basically One For each table 

Questions:
* How do classes interact with each other, especially with piping methods into and out of different classes? 
* Are there other reused classes like user and match? (Maybe within the breakdown of the data from API to Database



Classes Relative to use-case
Use Case Scenario 1: Creating a database for analysis and ML Modeling
Steps
1. Query for a specific subset of users based on REGION and RANK
1. Store Match information (Duplicate Match IDs should be checked and skipped for optimization)
1. Store Ranking information (difficult, rank over time is not stored. Best way would be to query that data seperately every 30 mins) [Push to Next Version]


Use Case Scenario 2: Looking up users within my match
1. Query for match history based on manually inputted usernames
1. Store Match Database for Analysis
1. Run analysis ("this person's top 3 comps are ... and have ... TOP 4%. )"
1. Utilize "ML model" for prediction


# Overview

## Objective

## ETL Process
1. EXTRACT - API Configuration
1. TRANSFORM - Data Munging Userprofiles and TFT Matches 
1. LOAD - SQLAlchemy Insertion into Storage Database

## Data Analysis and Modeling
1. Comparisons per Rank and Region
    * Hypothesis
        * As Rank increases, competition becomes tighter
        * Different regions have noticably different playstyles/metas
    
    * Hypothetical Root Causes:
        * Rank - Higher rank will show less gold remaining when Health reaches 0
        * Rank - Higher rank will show shorter stages of the game
    
    * Hypothetical Solutions:
1. "What makes BOT4?" 
    * Hypothesis: Inaccurate player understanding of their comp powerlevel relative to other players
        * Playing too greedy when actually terminally weak
    * Hypothetical Root Causes:
        * 
    * Hypothetical Solutions:
        * Access damage dealt is above "some threshold" by "some stage in the game"

1. "What is the optimal setup for comps?"
    * Example: For Sharpshooters how much higher is the average placement for Teemo Chosen vs Vayne Chosen
1. Conditional Matches
    * If a match was close what are "good enough" comps
    * If contested, which comps do better
 
## Implementation for Competitive Usage
1. Basic analytics per User output, expose one-trick players
1. Suggest counter comps


## Summary

---

# ETL 

In [1]:
# https://pypi.org/project/ratelimit/
from ratelimit import limits, sleep_and_retry

In [2]:
# Decorator factory to merge the decorators together!
def API_CALL_LIMIT():
    
    #https://developer.riotgames.com/
    #Rate Limits
    # HIGHEST BOUND: 50 per min
    # 20 requests every 1 seconds(s)
    requests = 20
    #rate_limit = 1
    rate_limit = 2
    #100 requests every 2 minutes(s)
    requests_2 = 100
    #rate_limit_2 = 120
    rate_limit_2 = 180
    deco2 = limits(calls=requests, period=rate_limit)
    deco1 = limits(calls=requests_2, period=rate_limit_2)

    def combined_decorator(func):
        return sleep_and_retry(deco2(deco1(func)))

    return combined_decorator

In [3]:
# Libraries
import requests

import pprint
pp = pprint.PrettyPrinter(depth=8)

import time

import sqlalchemy as db

# how to connect to local? I think I need a driver to do so
# https://www.youtube.com/watch?v=qfYzCdkVwig
# pip installed pymysql
# https://towardsdatascience.com/sqlalchemy-python-tutorial-79a577141a91

import pymysql
# import json # Requests already converts JSON into dict

In [4]:
# Api Key Needs to be changed every couple of days!!!!
    #api_key = "EXAMPLE-NUMBERS-LETTERS-UPPERCASE-LOWERCASE"
# Header for API queries

# https://www.tutorialexample.com/jupyter-notebook-run-python-script-py-file-and-command-line-a-simple-guide/
%run config.py

# Database Setup
Setup for Local mysqldb server

In [5]:
engine = db.create_engine("mysql+pymysql://root@localhost/TFT", echo = True) #Set echo to False to hide outputs
conn = engine.connect()

2020-12-26 20:06:32,156 INFO sqlalchemy.engine.base.Engine SHOW VARIABLES LIKE 'sql_mode'
2020-12-26 20:06:32,159 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:06:32,161 INFO sqlalchemy.engine.base.Engine SHOW VARIABLES LIKE 'lower_case_table_names'
2020-12-26 20:06:32,162 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:06:32,166 INFO sqlalchemy.engine.base.Engine SELECT DATABASE()
2020-12-26 20:06:32,166 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:06:32,167 INFO sqlalchemy.engine.base.Engine show collation where `Charset` = 'utf8mb4' and `Collation` = 'utf8mb4_bin'
2020-12-26 20:06:32,168 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:06:32,169 INFO sqlalchemy.engine.base.Engine SELECT CAST('test plain returns' AS CHAR(60)) AS anon_1
2020-12-26 20:06:32,170 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:06:32,171 INFO sqlalchemy.engine.base.Engine SELECT CAST('test unicode returns' AS CHAR(60)) AS anon_1
2020-12-26 20:06:32,172 INFO sqlalchemy.engine.base.E

## SQLALCHEMY Referencing Tables

In [33]:
meta = db.MetaData()
# engine.execute("CREATE TABLE items (item_id int, item_name varchar(255))")
items = db.Table(
    'items', meta, 
    db.Column('item_id', db.Integer, primary_key = True, autoincrement = False), 
    db.Column('item_name', db.String(255))
)
#engine.execute("CREATE TABLE match_id (match_id int, game_datetime datetime, game_length int, game_version varchar(255))")
match_id = db.Table(
    'match_id', meta,
    db.Column('match_id', db.Integer, primary_key = True, autoincrement = False),
    db.Column('game_datetime', db.DateTime),
    db.Column('game_length', db.Integer, autoincrement = False),
    db.Column('game_version', db.String(255))
)

#engine.execute("CREATE TABLE match_info (match_id int, puuid varchar(255), placement int, level int, "
#                                       "time_eliminated int, last_round int, gold_left int, total_damage_to_players int,"
#                                        "traits varchar(255), chosen_info varchar(255), units varchar(255))")


match_info = db.Table(
    'match_info', meta,
    db.Column('match_id', db.Integer, primary_key = True, autoincrement = False),
    db.Column('puuid', db.String(255)),
    db.Column('placement', db.Integer, autoincrement = False),
    db.Column('level', db.Integer, autoincrement = False),
    db.Column('time_eliminated', db.Integer, autoincrement = False),
    db.Column('gold_left', db.Integer, autoincrement = False),
    db.Column('total_damage_to_players', db.Integer, autoincrement = False),
    db.Column('traits', db.String(255)),
    db.Column('chosen_info', db.String(255)),
    db.Column('units', db.String(255))
)

#engine.execute("CREATE TABLE user_info (puuid varchar(255), summoner_id varchar(255), summoner_username varchar(255))")
user_info = db.Table(
    'user_info', meta,
    db.Column('puuid', db.String(255), index=True),
    db.Column('summoner_id', db.String(255), index=True),
    db.Column('summoner_username', db.String(255)),
    db.UniqueConstraint('puuid'),
    db.UniqueConstraint('summoner_id'),
    db.UniqueConstraint('summoner_username')
)

#engine.execute("CREATE TABLE user_rank (summoner_id varchar(255), tier varchar(255), rank varchar(255), league_points int, revision_date datetime)")
user_rank = db.Table(
    'user_rank', meta,
    db.Column('summoner_id', db.String(255), index=True),
    db.Column('time_searched', db.Float),
    db.Column('tier', db.String(5)),
    db.Column('rank', db.String(10)),
    db.Column('league_points', db.Integer),
    db.Column('wins', db.Integer),
    db.Column('losses', db.Integer),
    db.Column('fresh_blood', db.Boolean),
    db.Column('hot_streak', db.Boolean),
    db.Column('veteran', db.Boolean),
    db.Column('inactive', db.Boolean)
)

## Creating the Tables
First-time creation

In [34]:
meta.create_all(engine)

2020-12-26 20:44:33,751 INFO sqlalchemy.engine.base.Engine DESCRIBE `items`
2020-12-26 20:44:33,752 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:44:33,769 INFO sqlalchemy.engine.base.Engine DESCRIBE `match_id`
2020-12-26 20:44:33,770 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:44:33,783 INFO sqlalchemy.engine.base.Engine DESCRIBE `match_info`
2020-12-26 20:44:33,783 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:44:33,795 INFO sqlalchemy.engine.base.Engine DESCRIBE `user_info`
2020-12-26 20:44:33,796 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:44:33,805 INFO sqlalchemy.engine.base.Engine ROLLBACK
2020-12-26 20:44:33,805 INFO sqlalchemy.engine.base.Engine DESCRIBE `user_rank`
2020-12-26 20:44:33,805 INFO sqlalchemy.engine.base.Engine {}
2020-12-26 20:44:33,818 INFO sqlalchemy.engine.base.Engine 
CREATE TABLE user_info (
	puuid VARCHAR(255), 
	summoner_id VARCHAR(255), 
	summoner_username VARCHAR(255), 
	UNIQUE (puuid), 
	UNIQUE (summoner_id), 
	UNIQUE (summon

## Testing SQL Functionality

### Inserting

In [8]:
# https://docs.sqlalchemy.org/en/14/core/dml.html
# Inserting
# if one of them is already found, then all of it wont work
def insert_test1():
    try:
        conn.execute(user_rank.insert(), [
            {'summoner_id': 'A', 
             'time_searched':1608683566.2611852,
             'tier':'PLATINUM',
             'rank':'I',
             'league_points':1000,
             'wins':1000,
             'losses':1,
             'fresh_blood':False,
             'hot_streak':False,
             'veteran':False,
             'inactive':False
            }
         ])
    except db.exc.IntegrityError:
        print("An IntegrityError exception occurred. Already in Database") 

    


In [9]:
def insert_test2():
    try:
        conn.execute(user_info.insert(), [
            {
            'puuid': None, #Python None = SQL NULL
            'summoner_id':1,
            'summoner_username':'TEST',
            }
         ])
    except db.exc.IntegrityError:
        print("An IntegrityError exception occurred. Already in Database") 


### Selecting

In [10]:
# https://towardsdatascience.com/sqlalchemy-python-tutorial-79a577141a91
def select_test1():
    query = db.select([user_info.columns.summoner_id]).where(user_info.c.puuid == None)
    Result = conn.execute(query)
    
    for row in Result:
        print(row.values()[0])
        print(type(row.values()[0]))

In [11]:
#select_test1()

### Updating

In [12]:
def update_test1():
    query = db.update(user_info).where(user_info.c.summoner_id == "1").values({"puuid":"TESTpuuid"})
    Result = conn.execute(query)
    
#     for row in Result:
#         print(row.values()[0])
#         print(type(row.values()[0]))

In [13]:
#update_test1()

In [35]:
# API response dictionary (human readable errors)
API_Responses = {
    200: "OK",
    400: "Bad request",
    401: "Unauthorized",
    403: "Forbidden",
    404: "Data not found",
    405: "Method not allowed",
    415: "Unsupported media type",
    429: "Rate limit exceeded",
    500: "Internal server error",
    502: "Bad gateway",
    503: "Service unavailable",
    504: "Gateway timeout"
}
# TODO Create error handling depending on API response


In [46]:
# LOOP I: Iterate through each PAGE
@API_CALL_LIMIT()
def search_rank(rank, tier, page):
    """
    Output a list of dicts, where each list item is a user with a dict of profile values
    """
    search_rank = "https://na1.api.riotgames.com/tft/league/v1/entries/{}/{}?page={}".format(rank, tier, page)
    response_search_rank = requests.get(search_rank, headers=headers)
    if API_Responses[response_search_rank.status_code] == "OK":
        return response_search_rank.json()
    else:
        return "ERROR"
    

In [60]:

page = 1
rank = "DIAMOND" # PLATINUM, GOLD, SLIVER, BRONZE, IRON
tier = "I" # I, II, III, IV
time_searched = time.time()

def create_search_rank_pages(page, rank, tier):
    search_rank_pages = {}
    while True:
        #print(page) #try-catch-else?
        page_info = search_rank(rank, tier, page)
        # Error handling
        if page_info == "ERROR":
            print("Connection Issue")
            break
        elif page_info == []:
            print("Total Pages: {}".format(page-1))
            break
        else:
            search_rank_pages[page] = page_info
            page += 1
    return search_rank_pages

In [61]:
pages = create_search_rank_pages(page, rank, tier)

Total Pages: 17


In [49]:
def insert_user_rank_and_user_info(page, rank, tier, time_searched, search_rank_pages):
    page_number = 1
    count = 1
    for pages in search_rank_pages:
        for user in search_rank_pages[pages]:
            summoner_id = user['summonerId']
            summoner_name = user['summonerName']
            #league_id = user['leagueId']

            league_points = user['leaguePoints']
            tier = tier
            rank = rank
            wins = user['wins']
            losses = user['losses']
            fresh_blood = user['freshBlood']
            hot_streak = user['hotStreak']
            veteran = user['veteran']
            inactive = user['inactive']


    #         count +=1
    #         print("{},{},{}".format(summoner_id,summoner_name,league_id))
    #         print("{},{},{}".format(tier,rank,league_points))
    #         print("{},{},{},{},{},{}".format(wins,losses,fresh_blood,hot_streak,veteran,inactive))
    #         print(page_number)
    #         print(userpage)
    #         print(len(search_rank_pages[page_number]))
    #         print(userpage)
            try:
                conn.execute(user_rank.insert(), [
                    {
                    'summoner_id': summoner_id, 
                    'time_searched':time_searched,
                    'tier':tier,
                    'rank':rank,
                    'league_points':league_points,
                    'wins':wins,
                    'losses':losses,
                    'fresh_blood':fresh_blood,
                    'hot_streak':hot_streak,
                    'veteran':veteran,
                    'inactive':inactive
                    }
                 ])
            except db.exc.IntegrityError:
                print("An IntegrityError exception occurred. Already in user_rank Database")

            try:
                conn.execute(user_info.insert(), [
                    {
                    'puuid': None, 
                    'summoner_id':summoner_id,
                    'summoner_username':summoner_name,
                    }
                 ])
            except db.exc.IntegrityError:
                print("An IntegrityError exception occurred. Already in user_info Database") 


        page_number += 1
    #   print(page_number)

    # print(count)

In [63]:
insert_user_rank_and_user_info(page, rank, tier, time_searched, pages)

2020-12-26 21:35:43,176 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_points, wins, losses, fresh_blood, hot_streak, veteran, inactive) VALUES (%(summoner_id)s, %(time_searched)s, %(tier)s, %(rank)s, %(league_points)s, %(wins)s, %(losses)s, %(fresh_blood)s, %(hot_streak)s, %(veteran)s, %(inactive)s)
2020-12-26 21:35:43,176 INFO sqlalchemy.engine.base.Engine {'summoner_id': '96NBb7NS12i-NxYO4gZEyfjla6AtKRNm3MtI5a0vxBGO1fK9', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 0, 'wins': 77, 'losses': 592, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:35:43,187 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:35:43,191 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:35:43,192 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_

2020-12-26 21:35:43,254 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'pS2oDyA_Cv34v8hko6obKM1mu6aTXv3Qc8eTaEVoyinT5-9M', 'summoner_username': 'LivingPurple'}
2020-12-26 21:35:43,256 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:35:43,258 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_points, wins, losses, fresh_blood, hot_streak, veteran, inactive) VALUES (%(summoner_id)s, %(time_searched)s, %(tier)s, %(rank)s, %(league_points)s, %(wins)s, %(losses)s, %(fresh_blood)s, %(hot_streak)s, %(veteran)s, %(inactive)s)
2020-12-26 21:35:43,258 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'LZD1bU-zEB7ygCFHosTiBRDHgy2B0tlwvDU8IPlvXqgvpJIP', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 0, 'wins': 24, 'losses': 167, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:35

2020-12-26 21:35:43,313 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:35:43,315 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:35:43,316 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'K_rlMGAvz3CgDtGHKWo8G90IktdeNYYx6DxMQS3Xg89DMIAE', 'summoner_username': 'RageOn Rondo'}
2020-12-26 21:35:43,317 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:35:43,319 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_points, wins, losses, fresh_blood, hot_streak, veteran, inactive) VALUES (%(summoner_id)s, %(time_searched)s, %(tier)s, %(rank)s, %(league_points)s, %(wins)s, %(losses)s, %(fresh_blood)s, %(hot_streak)s, %(veteran)s, %(inactive)s)
2020-12-26 21:35:43,320 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'M

2020-12-26 21:35:43,373 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'oIqN3aIIoVIf16AgWBBQ8kskSOPiiSR-J24KyGh8QQGrGGC0', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 43, 'wins': 17, 'losses': 130, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:35:43,375 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:35:43,376 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:35:43,377 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'oIqN3aIIoVIf16AgWBBQ8kskSOPiiSR-J24KyGh8QQGrGGC0', 'summoner_username': 'Great China 69'}
2020-12-26 21:35:43,378 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:35:43,382 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, leagu

2020-12-26 21:35:43,431 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'p-FSO4bUs5JI6Z7096mHVqnmvdBXLzsCQqUvsr8QaVuE8EK6', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 0, 'wins': 23, 'losses': 73, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:35:43,432 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:35:43,434 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:35:43,434 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'p-FSO4bUs5JI6Z7096mHVqnmvdBXLzsCQqUvsr8QaVuE8EK6', 'summoner_username': 'exhotspro'}
2020-12-26 21:35:43,436 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:35:43,441 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_point

...

2020-12-26 21:36:09,307 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'cVk4gFQszVSQM8oiVMDJL5bVC_brqSWrfKoiNgBbzJHLTIo', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 69, 'wins': 27, 'losses': 118, 'fresh_blood': 1, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:36:09,308 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:36:09,310 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:36:09,310 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'cVk4gFQszVSQM8oiVMDJL5bVC_brqSWrfKoiNgBbzJHLTIo', 'summoner_username': 'Cold Tick'}
2020-12-26 21:36:09,311 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:36:09,314 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_point

2020-12-26 21:36:09,362 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'j3-v_VxbZ02SNk5o8BFwmpjYKGWucEsQ4urQADbV5Q-pqkE', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 8, 'wins': 34, 'losses': 203, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:36:09,363 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:36:09,365 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:36:09,365 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'j3-v_VxbZ02SNk5o8BFwmpjYKGWucEsQ4urQADbV5Q-pqkE', 'summoner_username': 'fwme'}
2020-12-26 21:36:09,367 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:36:09,369 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_points, win

2020-12-26 21:36:09,414 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'lh9N_BXPGSYszZ7obME_bbYh9_Vr4fAhsb4mZiC3ct7_yZw', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 50, 'wins': 28, 'losses': 160, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:36:09,416 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:36:09,417 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:36:09,418 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'lh9N_BXPGSYszZ7obME_bbYh9_Vr4fAhsb4mZiC3ct7_yZw', 'summoner_username': 'Liberaltarianism'}
2020-12-26 21:36:09,419 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:36:09,421 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, leagu

2020-12-26 21:36:09,463 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'U_3Ia9ryvf08dFSZSCuWJiXYcIJaiVUxtTET7QvsmaLK7ys', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 75, 'wins': 34, 'losses': 163, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:36:09,464 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:36:09,466 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:36:09,466 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'U_3Ia9ryvf08dFSZSCuWJiXYcIJaiVUxtTET7QvsmaLK7ys', 'summoner_username': 'IceInMyVein'}
2020-12-26 21:36:09,467 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database
2020-12-26 21:36:09,469 INFO sqlalchemy.engine.base.Engine INSERT INTO user_rank (summoner_id, time_searched, tier, `rank`, league_poi

2020-12-26 21:36:09,513 INFO sqlalchemy.engine.base.Engine {'summoner_id': 'rsU5hFCoMg7VPCK3QkZ3Mt5nRiCsqKKVuNQCfPhCbUAyW7Y', 'time_searched': 1609046786.4506164, 'tier': 'I', 'rank': 'DIAMOND', 'league_points': 17, 'wins': 35, 'losses': 175, 'fresh_blood': 0, 'hot_streak': 0, 'veteran': 0, 'inactive': 0}
2020-12-26 21:36:09,515 INFO sqlalchemy.engine.base.Engine COMMIT
2020-12-26 21:36:09,516 INFO sqlalchemy.engine.base.Engine INSERT INTO user_info (puuid, summoner_id, summoner_username) VALUES (%(puuid)s, %(summoner_id)s, %(summoner_username)s)
2020-12-26 21:36:09,517 INFO sqlalchemy.engine.base.Engine {'puuid': None, 'summoner_id': 'rsU5hFCoMg7VPCK3QkZ3Mt5nRiCsqKKVuNQCfPhCbUAyW7Y', 'summoner_username': 'SÖRRY1'}
2020-12-26 21:36:09,518 INFO sqlalchemy.engine.base.Engine ROLLBACK
An IntegrityError exception occurred. Already in user_info Database


In [41]:
@API_CALL_LIMIT()
def search_puuid(summoner_id):
    """
    Output a dict where each item is a user profile value
    """
    search_puuid = "https://na1.api.riotgames.com/tft/summoner/v1/summoners/{}".format(summoner_id)
    response_search_puuid = requests.get(search_puuid, headers=headers)
    if API_Responses[response_search_puuid.status_code] == "OK":
        return response_search_puuid.json()
    else:
        return "ERROR"


In [42]:
def update_puuid():
    """
    Update user_info database with puuids based on their summoner_id
    
    """
    # Select summonerIDs that do not have puuids
    query = db.select([user_info.columns.summoner_id]).where(user_info.c.puuid == None)
    Result = conn.execute(query)
   
    if Result == None:
        print("All puuids updated!")
        pass
    else:
        print("Updating puuids")
        print(Result)
        for row in Result:
            print(row.values()[0])
            #print(type(row.values()[0]))
            
            summoner_id = row.values()[0]
            # Query profile info using summonerID
            user_profile_info = search_puuid(summoner_id)

            puuid = user_profile_info['puuid']
            
            # Insert puuid into user data DB
            # Error handling
            if user_profile_info == "ERROR":
                print("Connection Issue")
                break
            else:
                try:
                    conn.execute(db.update(user_info).where(user_info.c.summoner_id == summoner_id).values({"puuid":puuid}))
                except db.exc.IntegrityError:
                     print("An IntegrityError exception occurred. Already in user_info Database") 

        

In [67]:
update_puuid()

2020-12-26 21:50:40,053 INFO sqlalchemy.engine.base.Engine SELECT user_info.summoner_id 
FROM user_info 
WHERE user_info.puuid IS NULL
2020-12-26 21:50:40,054 INFO sqlalchemy.engine.base.Engine {}
Updating puuids
cNfuouCx7LOiqDN97LEYh6624naduuMRkWxz9V5dpVQRNzKu
2020-12-26 21:50:40,348 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:40,350 INFO sqlalchemy.engine.base.Engine {'puuid': 'GNRgazhahP5gkULLd_LbqIlKBZ0PTEqIFkXAUXzbMk-0fZKYZieiBlJzaBnwm495Oe4wV_NsMCLpXQ', 'summoner_id_1': 'cNfuouCx7LOiqDN97LEYh6624naduuMRkWxz9V5dpVQRNzKu'}
2020-12-26 21:50:40,355 INFO sqlalchemy.engine.base.Engine COMMIT
hu3yqrKLdSm7RD5ZTMeHHcxJ9Nklsk9N2u2iM9eLpf6vXPJO
2020-12-26 21:50:40,558 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:40,561 INFO sqlalchemy.engine.base.Engine {'puuid': 'sAdIZ4xxwGhFNcETMZ_pmMVfjR8J8m1XBqY_gunCACP0K

2020-12-26 21:50:43,567 INFO sqlalchemy.engine.base.Engine COMMIT
kEnQbe_ndMKcnpQFPZH1tFKA-gIdUw3lYBbwNO1LcDkGsiGR
2020-12-26 21:50:43,766 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:43,770 INFO sqlalchemy.engine.base.Engine {'puuid': 'XQ-hx-I9yDZBgcSaqD1FQ_dBKTfLFsW1zgdusW1DmBSnhn7yQpKARADh0mI80tT3KrYzEbj-2hMjlA', 'summoner_id_1': 'kEnQbe_ndMKcnpQFPZH1tFKA-gIdUw3lYBbwNO1LcDkGsiGR'}
2020-12-26 21:50:43,777 INFO sqlalchemy.engine.base.Engine COMMIT
LYGp5MfOc7JP_7IsuddYoKSTPRBQpV32XuxzLkWyCm1yo6ea
2020-12-26 21:50:43,967 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:43,969 INFO sqlalchemy.engine.base.Engine {'puuid': 'sndP7L5rM9My18rKfftjqE3dQBN_2sZn1-UEtFAAYj_BayjJUal2rMIX33C6XKTB4eFcET99NveC4A', 'summoner_id_1': 'LYGp5MfOc7JP_7IsuddYoKSTPRBQpV32XuxzLkWyCm1yo6ea'}
2020-12-26 21:50:43,971 INFO sqlalchemy.en

6lekGetI6xaVe3NZfS_axHdASCo-BPHaUE6smhaRSRQzoyim
2020-12-26 21:50:47,101 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:47,103 INFO sqlalchemy.engine.base.Engine {'puuid': '9K6NIV8QPgNmoYfqJ0mcy8kVYfIHujLe4xhNW7eTKT1lcajEf7Qw5TxKA5oxfqK-vWF_6X08YoqXVw', 'summoner_id_1': '6lekGetI6xaVe3NZfS_axHdASCo-BPHaUE6smhaRSRQzoyim'}
2020-12-26 21:50:47,106 INFO sqlalchemy.engine.base.Engine COMMIT
c2t_G1nat-kqUjnzC2Mqd7piHuvuyZ2uyORNGO78L9mVLJ5x
2020-12-26 21:50:47,290 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:47,292 INFO sqlalchemy.engine.base.Engine {'puuid': '1dh3e_Nyeri5ECyXx_t5PXUiMMfYKa9NjUoMlGPclcuqdwjOsM9h1zKwXAkyUvw7Eyqa9nLGVg4Qog', 'summoner_id_1': 'c2t_G1nat-kqUjnzC2Mqd7piHuvuyZ2uyORNGO78L9mVLJ5x'}
2020-12-26 21:50:47,295 INFO sqlalchemy.engine.base.Engine COMMIT
UgTjvp_N5qxyePbqt1qCWP3yfgiLS4HekRMeR3qxeq

2020-12-26 21:50:50,599 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:50,602 INFO sqlalchemy.engine.base.Engine {'puuid': 'PNmbVEte86KMMEsEpWmhpF5B2WgoC0yhIRIhF08U2teidrUcyogFBv1_CuIgzfaYj-O7e8py1Hcz9Q', 'summoner_id_1': 'gyAXBxUuqoWFAGVzP8joctY-r0CGsCnhFZwYggy2U8_sxR5G'}
2020-12-26 21:50:50,606 INFO sqlalchemy.engine.base.Engine COMMIT
RXayRIk14uHvGDUVMc88_YbFxOzfiI-SrPNtsoC2AVFiH1Oo
2020-12-26 21:50:50,788 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:50,791 INFO sqlalchemy.engine.base.Engine {'puuid': 'MfhQxGjt7YnYsQcrGDc-INZS1XtAWhEIAPMwLh7rslIp9eMyA4Tqt2nfVGOc21ueajkaEjOPrVsCSw', 'summoner_id_1': 'RXayRIk14uHvGDUVMc88_YbFxOzfiI-SrPNtsoC2AVFiH1Oo'}
2020-12-26 21:50:50,800 INFO sqlalchemy.engine.base.Engine COMMIT
d_2ADU2OGGKpHmFFa6VMnk3RKPzlqFvKdeFHM-hZfZS3L7q1
2020-12-26 21:50:50,999 INFO sqlalchemy.en

2020-12-26 21:50:53,989 INFO sqlalchemy.engine.base.Engine {'puuid': 'hVJxRqTer-D6h2BNIFNPgQTv6rd6JKOHZjgiRLjFsQ_SFT5M56vLM9PPGkfTTZ_ouFw7Lv_7nuWL4g', 'summoner_id_1': '-UAXLvb7xI5nqSnG016lITDmNAcN2qhB1E02sRApjgmjg47b'}
2020-12-26 21:50:53,990 INFO sqlalchemy.engine.base.Engine COMMIT
q_-j-fJytIuHxsacDxQeC-k-Pf0441Gg4ihFdT5FFwn8BZFo
2020-12-26 21:50:54,183 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:54,183 INFO sqlalchemy.engine.base.Engine {'puuid': 'p3aid9LZniWBwqEDfKjdF1P6fFiSdvBftDu-CxlRQly9X83BbZ4t23N6ev73joQtlNyHNpFFcPIyow', 'summoner_id_1': 'q_-j-fJytIuHxsacDxQeC-k-Pf0441Gg4ihFdT5FFwn8BZFo'}
2020-12-26 21:50:54,185 INFO sqlalchemy.engine.base.Engine COMMIT
g91TsZZNI6JjdynxhWcsz52EfGKGqdVT1nKKT1dqcbCyJFpd
2020-12-26 21:50:54,378 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 21:50:54,379 INFO sqlalchemy.en

...

2020-12-26 23:20:49,146 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:49,147 INFO sqlalchemy.engine.base.Engine {'puuid': 'rOofwDe39S8P8vMtWi5Wx_EPL0351IcwiW9ghg5B4ex2CWGE4jPDrT2DbrcVY__rlAg-VviSHM1msA', 'summoner_id_1': 'HPjTmQkJtjPXxroyKwDDnPPuyvXZjGcLlYyeWlPonC__rxk'}
2020-12-26 23:20:49,150 INFO sqlalchemy.engine.base.Engine COMMIT
E3altYdvkSSUaTxbIG7vN23sjLjtLhiAPp6pqkVS83CXw4s
2020-12-26 23:20:49,341 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:49,342 INFO sqlalchemy.engine.base.Engine {'puuid': 'JLQ-wdVvCMbkWsHKAsHIr6KIC0HD5BOGzztU8lVUWrJM6OHkS_0b7JBsVUm4T5qoa4D3qLAnE5wnmg', 'summoner_id_1': 'E3altYdvkSSUaTxbIG7vN23sjLjtLhiAPp6pqkVS83CXw4s'}
2020-12-26 23:20:49,344 INFO sqlalchemy.engine.base.Engine COMMIT
12vAAV5opoQssoXl5juv0OftaW4P55puDCNkgubHQu8E-Xw
2020-12-26 23:20:49,526 INFO sqlalchemy.engine

2020-12-26 23:20:52,386 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:52,387 INFO sqlalchemy.engine.base.Engine {'puuid': '4_QEQL_43amqZy2ROrTLhFK3RElSto2yOxYM8DiUs1CQJ-8wXhcLhqIByZA2Jwdf81aFW03OQRzWyQ', 'summoner_id_1': 'TOSJGuhNGOGaYvHI9La9CctJnA4nHUDfPnmggeGLmydEy8w'}
2020-12-26 23:20:52,388 INFO sqlalchemy.engine.base.Engine COMMIT
a2vu8LjuBkQffrX-sEWrBxhBUom_o2RlYdKNxIZuyrmERug
2020-12-26 23:20:52,568 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:52,569 INFO sqlalchemy.engine.base.Engine {'puuid': 'btELE6TrL4VHhAU0ruo5DCC2Ki4KlfrodaQ8EodaE6FqCe8dzUyZrhWXf-Ct_qfrdS9pji2RPEs4tQ', 'summoner_id_1': 'a2vu8LjuBkQffrX-sEWrBxhBUom_o2RlYdKNxIZuyrmERug'}
2020-12-26 23:20:52,571 INFO sqlalchemy.engine.base.Engine COMMIT
x4iWJBNm_3ti6YP7WJl6sFQOW_H5IpgjWvKBEn0FwBfremw
2020-12-26 23:20:52,760 INFO sqlalchemy.engine

2020-12-26 23:20:55,686 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:55,686 INFO sqlalchemy.engine.base.Engine {'puuid': 'REUeUAK0TvyJ1vb2Hc3PSzZJ62g335sqL_1C67Pa6uVk51g-dyx68-jzqh16HxaQiqDKMcyvDqbsWA', 'summoner_id_1': '4syoPhurvtgbJ1eG8uEXG1I6I9lyKxo7JE7SJ1gWiwLRG0w'}
2020-12-26 23:20:55,688 INFO sqlalchemy.engine.base.Engine COMMIT
u-Vyj6gM2jU0tIHu4-_nh1lREASRdt3seqpJnT1-V1l6LMw
2020-12-26 23:20:55,862 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:55,862 INFO sqlalchemy.engine.base.Engine {'puuid': 'SqwjFBRhDRE3YTRW4inslU8ssCwSNEkEGfseTxoeGahFaB_zR2unSq_vB6O-1wmupckiwlZQLphKNg', 'summoner_id_1': 'u-Vyj6gM2jU0tIHu4-_nh1lREASRdt3seqpJnT1-V1l6LMw'}
2020-12-26 23:20:55,864 INFO sqlalchemy.engine.base.Engine COMMIT
Kofb7LueX38-JXVWMhK3PaU6D55ARyHflTwxwe1tSX0jRfM
2020-12-26 23:20:56,047 INFO sqlalchemy.engine

2020-12-26 23:20:58,813 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:58,813 INFO sqlalchemy.engine.base.Engine {'puuid': 'B6bLxQ7_dFv116kgG8mHf8NjeOH25aKW3q3Ot_ZGxcEGXjirth6wuNdhKUWL2kVBp4J4dein3sXmvw', 'summoner_id_1': '8Y6q3Z7zQdbK698goIuTwKN6U9lvbihQ-6J6sUYaZ7XqiOQ'}
2020-12-26 23:20:58,814 INFO sqlalchemy.engine.base.Engine COMMIT
HbGTNRfRhZF4SSqHR64-dhlDr3XPJHCtWbBGh9L69mDKsbE
2020-12-26 23:20:59,016 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:20:59,016 INFO sqlalchemy.engine.base.Engine {'puuid': 'FWUUteR_FJrqAc1WYaXM9B5EBV-iG_Tc-b6OFFvmGPWud6u7z30h4txqouGxxAQRBuzlH5TAQtKVWg', 'summoner_id_1': 'HbGTNRfRhZF4SSqHR64-dhlDr3XPJHCtWbBGh9L69mDKsbE'}
2020-12-26 23:20:59,018 INFO sqlalchemy.engine.base.Engine COMMIT
n5e96c-i_iBz5h50PnanaV6Uw9wsfD_FiatfhZ2cmRdP0cg
2020-12-26 23:20:59,205 INFO sqlalchemy.engine

2020-12-26 23:23:42,939 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:23:42,940 INFO sqlalchemy.engine.base.Engine {'puuid': 'xtjtCxBlvk4-tiQlEWTrMwDEYKaXZxipt0K9BEh9t-yqMkw68vNgLg6l5srSIMocZ_lxx8kHXx75IA', 'summoner_id_1': 'Pg1YWIjsCB5S0NR1Qi_JCmhCt6v8letNkcV4_mPOi7rj-V4'}
2020-12-26 23:23:42,941 INFO sqlalchemy.engine.base.Engine COMMIT
lh9N_BXPGSYszZ7obME_bbYh9_Vr4fAhsb4mZiC3ct7_yZw
2020-12-26 23:23:43,115 INFO sqlalchemy.engine.base.Engine UPDATE user_info SET puuid=%(puuid)s WHERE user_info.summoner_id = %(summoner_id_1)s
2020-12-26 23:23:43,117 INFO sqlalchemy.engine.base.Engine {'puuid': 'ahhl1vU0xZ24kSr5tAC4H6Ueyth56G-h2jUIrqlpMzHSUA93-_VcNN3XBMAqM1JwJ6X8IRUR8e2byQ', 'summoner_id_1': 'lh9N_BXPGSYszZ7obME_bbYh9_Vr4fAhsb4mZiC3ct7_yZw'}
2020-12-26 23:23:43,119 INFO sqlalchemy.engine.base.Engine COMMIT
ebf8HdF45gHq2BVeKzGUFG7ZhakrT6O9B2pRk2pOW3vx0as
2020-12-26 23:23:43,293 INFO sqlalchemy.engine

In [ ]:
# Search_by_ranking
# LOOP I: Iterate through each PAGE
    # Get Time in epoch - For match game datetime
# LOOP II: Iterate through each USER
    # Breakdown the ranking per person
    # Insert into user data DB (Name, summonerID, puuid(NULL), leagueId)
    # Insert into rank data DB (tier, rank, lp, wins, losses, veteran)

# One-time use since puuid/summonerid are used for identification
# Search_by_puuid
    # From Search_by_ranking, Select username
    # Search by summonerID LINK: https://developer.riotgames.com/apis#tft-summoner-v1/GET_getBySummonerId
    # Get puuid
    # insert puuid into user data DB (Name, summonerID, puuid, leagueId)

# [1 query] Get TIER and Rank of page 1 
# JSON -> List of names () [n = total length of name list]
# [n queries] List of names -> last 20 matches list
# last 20 matches list -> remove duplicates [m = total length of match list]
# [n+m queries] for each match look up match information
# break down match information




In [64]:
@API_CALL_LIMIT()
def search_matchlist(puuid,n_recent_matches):
    """
    """
    search_match = "https://americas.api.riotgames.com/tft/match/v1/matches/by-puuid/" + puuid + "/ids?count="+ str(n_recent_matches)
    response_search_match = requests.get(search_match, headers=headers)
    if API_Responses[response_search_match.status_code] == "OK":
        response_search_match_dict = response_search_match.json()

        match_list = dict()
        # From 0 to n_recent_matches
        for number, match_id in enumerate(response_search_match_dict):
            match_list[number]= match_id

        return match_list
    else:
        return "ERROR"


In [66]:
search_matchlist("yjXElY4a5UOP2lGqc2N2hYQawqXV5klerhVgnpaDOVyEEUkw9MGqoxFERZYxA2YBqt-HkYGiecYgoA",2)


{0: 'NA1_3714029307', 1: 'NA1_3711416644'}

In [ ]:
# Test which is faster for the API 
# summoner_request or summonerId

from functools import wraps
from time import time


def timing(f):
    @wraps(f)
    def wrapper(*args, **kwargs):
        start = time()
        result = f(*args, **kwargs)
        end = time()
        print 'Elapsed time: {}'.format(end-start)
        return result
    return wrapper





In [4]:
# How to make a request for username
# use headers variable always? 
# NA only, probably different <>.api.riotgames.com 

summoner_request = "AutoBattleBot"
search_summoner = 'https://na1.api.riotgames.com/tft/summoner/v1/summoners/by-name/'+summoner_request


response_search_summoner = requests.get(search_summoner, headers=headers)
print(API_Responses[response_search_summoner.status_code])

# Should have some sort of verifcation
# Should have some sort of error code to response

OK


In [5]:
print(response_search_summoner.json())

{'id': 'eLVSC31XyJpUcssw1Xx14DeMCaXZNdXqM3N2qgNTTD1tzDD8', 'accountId': '9saQlcagNsGYGvRvGr8gZrvm1JdJRlQXQpQ2qVgdqYzxV1lee1ce_13l', 'puuid': 'PvVcIk6ij_ib-lFOp-euC__GoPz4GTim3dMXe1XdzBAEDXBgL5ElnUSJRBDNSE2_qAb2qULSoEDVjA', 'name': 'AutoBattleBot', 'profileIconId': 29, 'revisionDate': 1603349358000, 'summonerLevel': 1}


In [6]:
r = requests.head(url=search_summoner)
print(r.headers)

{'Content-Type': 'application/json;charset=utf-8', 'Date': 'Fri, 11 Dec 2020 05:30:22 GMT, Fri, 11 Dec 2020  05:30:22 GMT', 'X-Riot-Edge-Trace-Id': '7da30b49-7b4a-4e1f-9688-bedd515c5a25', 'Connection': 'keep-alive'}


In [27]:
# How we convert to JSON and parse through
# Guessing it should be fine because each header is easily searched on RIOT API and they won't change

response_search_summoner_dict = response_search_summoner.json()
# Player Universally Unique IDentifiers (newer way)
puuid = response_search_summoner_dict['puuid']
# summoner id - mroe region based identification (old way)
summoner_id = response_search_summoner_dict['id']

print("puuid: " + puuid)
print("summoner_id: " + summoner_id)

puuid: PvVcIk6ij_ib-lFOp-euC__GoPz4GTim3dMXe1XdzBAEDXBgL5ElnUSJRBDNSE2_qAb2qULSoEDVjA
summoner_id: eLVSC31XyJpUcssw1Xx14DeMCaXZNdXqM3N2qgNTTD1tzDD8


In [28]:
# Request ranking information based on summoner id

search_ranking = "https://na1.api.riotgames.com/tft/league/v1/entries/by-summoner/" + summoner_id

response_search_ranking = requests.get(search_ranking, headers=headers)
print(API_Responses[response_search_ranking.status_code])


OK


In [15]:
# returns a list! instead of a dictionary... so we'll need to fix it....
print(response_search_ranking.json()[0])

{'leagueId': '41343c48-50bd-4175-a877-95770e208f04', 'queueType': 'RANKED_TFT', 'tier': 'PLATINUM', 'rank': 'I', 'summonerId': 'MnEQ6BcFXhipHCnnuM344LZ8bJ7rqkN61pXGhmPWMw-k5PqW', 'summonerName': '88chwain', 'leaguePoints': 0, 'wins': 26, 'losses': 165, 'veteran': False, 'inactive': False, 'freshBlood': True, 'hotStreak': False}


In [16]:
response_search_ranking_dict = response_search_ranking.json()[0]
tier = response_search_ranking_dict['tier']
rank = response_search_ranking_dict['rank']
LP = response_search_ranking_dict['leaguePoints']
wins = response_search_ranking_dict['wins']
losses = response_search_ranking_dict['losses']

#unsure about these metrics
#veteran = response_search_ranking_dict['veteran']
#inactive = response_search_ranking_dict['inactive']
#freshBlood = response_search_ranking_dict['freshBlood']
#hotStreak = response_search_ranking_dict['hotStreak']

In [17]:
# Request for Match IDs based on puuid
n_recent_matches = 20
search_match = "https://americas.api.riotgames.com/tft/match/v1/matches/by-puuid/" + puuid + "/ids?count="+ str(n_recent_matches)

response_search_match = requests.get(search_match, headers=headers)
print(API_Responses[response_search_match.status_code])

OK


In [18]:
response_search_match_dict = response_search_match.json()
# Player Unique User Identification -Used instead of raw name
response_search_match_dict

match_list = dict()
# From 0 to n_recent_matches
for number, match_id in enumerate(response_search_match_dict):
    match_list[number]= match_id


In [19]:
match_list
#match_list[0]

{0: 'NA1_3630152875',
 1: 'NA1_3628829278',
 2: 'NA1_3628851759',
 3: 'NA1_3627838012',
 4: 'NA1_3627812452',
 5: 'NA1_3627501044',
 6: 'NA1_3626440134',
 7: 'NA1_3626341535',
 8: 'NA1_3626174069',
 9: 'NA1_3625892017',
 10: 'NA1_3624488945',
 11: 'NA1_3624530116',
 12: 'NA1_3624442500',
 13: 'NA1_3623568534',
 14: 'NA1_3623510920',
 15: 'NA1_3623422925',
 16: 'NA1_3623345978',
 17: 'NA1_3623289356',
 18: 'NA1_3623081923',
 19: 'NA1_3622906182'}

In [20]:
# Match Information
search_match_info = "https://americas.api.riotgames.com/tft/match/v1/matches/" + match_list[0]

response_search_match_info = requests.get(search_match_info, headers=headers)
print(API_Responses[response_search_match_info.status_code])

OK


In [21]:
response_search_match_info_dict = response_search_match_info.json()

In [22]:
print(response_search_match_info_dict)

{'metadata': {'data_version': '5', 'match_id': 'NA1_3630152875', 'participants': ['pLp88KkYvcbTnKevXUb33CMol_eJSWq4xHjgINLW5iegO3Wtg0sUSy6LSJe44HQasMW90D_90-4C3w', 'OmFkLrQBN-xs0haPk5ooh-g2Of5Or7nqyQlEh0G7ed2fTVYErqbfylYYKu7PHSMGWQ0jSluxKC3hFw', 'JzKl_pACMSDQ_bY38GvOAdCu62yAnU9AUyiTnwJThphb5X4HmLC0GiV7LP9zxXItY139Eri1blg3aw', 'ARzZ8ZIsfhefpafFh9gvDLXbpA6Ws30QDbmhoUs8K6xsw1GGVmhEHwWCuUw7TQ5a5cjU15p9VX7XWQ', '_ILPMfKQrbeIN6auqksi_ajKmXaiLqeSQyvZlAOycAGqlLzN8XlpmiMvIUfJ_8lx1Ag8ZE7lEOKIDA', 'ZgaJ0EurUEW_InpChbfGMZt6Oda24huCDe1deMX70ltmvMjQaARxoYnPv8JDi9xQGLRCOj20Rfn2Rw', 'BsTuu6EscV1ofuNOBzBIQMaYOaglXrAumTmjGWKq8CdcU3cmSxZczwcntma8eimh14JpYnVDm-6Rkg', 'idjfj6nouxMYDnkAbsUrzJyjYVcfMu7BkLKAtVXIZGsdTdU-22sevGQEqLJmYa8AgE3jcfi0oACcmQ']}, 'info': {'game_datetime': 1603498465558, 'game_length': 2052.78662109375, 'game_version': 'Version 10.21.339.2173 (Oct 09 2020/15:54:03) [PUBLIC] <Releases/10.21>', 'participants': [{'companion': {'content_ID': '64691b63-1603-443e-bde5-727148f440ed', 'skin_ID'

In [23]:
import pprint
pp = pprint.PrettyPrinter(depth=8)
pp.pprint(response_search_match_info_dict)

{'info': {'game_datetime': 1603498465558,
          'game_length': 2052.78662109375,
          'game_version': 'Version 10.21.339.2173 (Oct 09 2020/15:54:03) '
                          '[PUBLIC] <Releases/10.21>',
          'participants': [{'companion': {'content_ID': '64691b63-1603-443e-bde5-727148f440ed',
                                          'skin_ID': 4,
                                          'species': 'PetMiner'},
                            'gold_left': 1,
                            'last_round': 35,
                            'level': 8,
                            'placement': 2,
                            'players_eliminated': 0,
                            'puuid': 'pLp88KkYvcbTnKevXUb33CMol_eJSWq4xHjgINLW5iegO3Wtg0sUSy6LSJe44HQasMW90D_90-4C3w',
                            'time_eliminated': 2044.4974365234375,
                            'total_damage_to_players': 122,
                            'traits': [{'name': 'Cultist',
                                   

In [25]:
pp.pprint(response_search_match_info_dict['info']['participants'][0])

{'companion': {'content_ID': '64691b63-1603-443e-bde5-727148f440ed',
               'skin_ID': 4,
               'species': 'PetMiner'},
 'gold_left': 1,
 'last_round': 35,
 'level': 8,
 'placement': 2,
 'players_eliminated': 0,
 'puuid': 'pLp88KkYvcbTnKevXUb33CMol_eJSWq4xHjgINLW5iegO3Wtg0sUSy6LSJe44HQasMW90D_90-4C3w',
 'time_eliminated': 2044.4974365234375,
 'total_damage_to_players': 122,
 'traits': [{'name': 'Cultist',
             'num_units': 2,
             'style': 0,
             'tier_current': 0,
             'tier_total': 3},
            {'name': 'Fortune',
             'num_units': 1,
             'style': 0,
             'tier_current': 0,
             'tier_total': 2},
            {'name': 'Keeper',
             'num_units': 1,
             'style': 0,
             'tier_current': 0,
             'tier_total': 3},
            {'name': 'Set4_Adept',
             'num_units': 1,
             'style': 0,
             'tier_current': 0,
             'tier_total': 3},
        

In [28]:
response_search_match_info_dict['info']['participants'][0]['gold_left']
response_search_match_info_dict['info']['participants'][0]['last_round']
response_search_match_info_dict['info']['participants'][0]['level']
response_search_match_info_dict['info']['participants'][0]['placement']
response_search_match_info_dict['info']['participants'][0]['players_eliminated']
response_search_match_info_dict['info']['participants'][0]['puuid']
response_search_match_info_dict['info']['participants'][0]['time_eliminated']
response_search_match_info_dict['info']['participants'][0]['total_damage_to_players']


122

In [29]:
trait_tier = dict()
for trait in response_search_match_info_dict['info']['participants'][0]['traits']:
    trait_tier[trait['name']] =  trait['tier_current']

In [30]:
trait_tier

{'Cultist': 0,
 'Fortune': 0,
 'Keeper': 0,
 'Set4_Adept': 0,
 'Set4_Assassin': 2,
 'Set4_Mystic': 0,
 'Set4_Ninja': 2,
 'Set4_Shade': 2,
 'Set4_Tormented': 1,
 'Warlord': 0}

In [32]:
trait_tier_sorted = sorted(trait_tier.items(),  key=lambda x:x[1], reverse=True)
trait_tier_sorted

[('Set4_Assassin', 2),
 ('Set4_Ninja', 2),
 ('Set4_Shade', 2),
 ('Set4_Tormented', 1),
 ('Cultist', 0),
 ('Fortune', 0),
 ('Keeper', 0),
 ('Set4_Adept', 0),
 ('Set4_Mystic', 0),
 ('Warlord', 0)]

In [33]:
trait_tier_clean = dict(filter(lambda num: num[1] !=0, trait_tier_sorted))
trait_tier_clean

{'Set4_Assassin': 2, 'Set4_Ninja': 2, 'Set4_Shade': 2, 'Set4_Tormented': 1}

In [73]:
type(response_search_match_info_dict['info']['participants'][0]['units'])

list

In [74]:
type(response_search_match_info_dict['info']['participants'][0]['units'][0])

dict

In [78]:
response_search_match_info_dict['info']['participants'][0]['units'][0]['chosen']

'Sharpshooter'

In [34]:
newlist = sorted(response_search_match_info_dict['info']['participants'][0]['units'], key=lambda k: len(k['items']), reverse=True) 

In [35]:
newlist

[{'character_id': 'TFT4_Akali',
  'chosen': 'Set4_Assassin',
  'items': [22, 19, 44],
  'name': '',
  'rarity': 2,
  'tier': 3},
 {'character_id': 'TFT4_Katarina',
  'items': [45, 69, 13],
  'name': '',
  'rarity': 2,
  'tier': 2},
 {'character_id': 'TFT4_Kennen',
  'items': [35, 78],
  'name': '',
  'rarity': 2,
  'tier': 2},
 {'character_id': 'TFT4_Evelynn',
  'items': [47],
  'name': '',
  'rarity': 2,
  'tier': 2},
 {'character_id': 'TFT4_Shen',
  'items': [25],
  'name': '',
  'rarity': 3,
  'tier': 2},
 {'character_id': 'TFT4_Zed', 'items': [], 'name': '', 'rarity': 1, 'tier': 2},
 {'character_id': 'TFT4_Pyke',
  'items': [],
  'name': '',
  'rarity': 1,
  'tier': 1},
 {'character_id': 'TFT4_Kayn',
  'items': [],
  'name': '',
  'rarity': 4,
  'tier': 1}]

In [36]:
itemization_dict = {
    0: "Not Itemized",
    1: "Partially Itemized",
    2: "Semi Itemized",
    3: "Fully Itemized"
    
}

In [37]:
chosen_info = ""

for i in newlist:
    if 'chosen' in i:
#        print(1)
        #print(i['character_id'])
        #print(i['tier'])
        chosen_info += i['chosen'] + " "
        chosen_info +=i ['character_id'] + " "
        if i['tier'] > 2:
            chosen_info += "Upgraded" + " "
        #print(i['items'])
        chosen_info += itemization_dict[len(i['items'])]
        
        print(chosen_info)
            

Set4_Assassin TFT4_Akali Upgraded Fully Itemized


In [55]:
response_search_match_info_dict['info']['participants'][0]['units'] # this is a list

response_search_match_info_dict['info']['participants'][0]['units'][0] #this is a dict


# List of units order by 
#chosen (Save this as variable for naming purposes later) # Regex
#number of items (count this list)
#tier
#rarity



[{'character_id': 'TFT4_Nidalee',
  'chosen': 'Sharpshooter',
  'items': [99, 35, 23],
  'name': '',
  'rarity': 0,
  'tier': 3},
 {'character_id': 'TFT4_Vayne',
  'items': [],
  'name': '',
  'rarity': 0,
  'tier': 1},
 {'character_id': 'TFT4_Teemo',
  'items': [37],
  'name': '',
  'rarity': 1,
  'tier': 3},
 {'character_id': 'TFT4_Thresh',
  'items': [],
  'name': '',
  'rarity': 1,
  'tier': 3},
 {'character_id': 'TFT4_Jinx',
  'items': [23, 14, 69],
  'name': '',
  'rarity': 2,
  'tier': 2},
 {'character_id': 'TFT4_Sejuani',
  'items': [37, 39, 44],
  'name': '',
  'rarity': 3,
  'tier': 2},
 {'character_id': 'TFT4_Jhin',
  'items': [17, 35, 12],
  'name': '',
  'rarity': 3,
  'tier': 2},
 {'character_id': 'TFT4_Azir',
  'items': [22],
  'name': '',
  'rarity': 4,
  'tier': 1}]

SQL TABLES

Username Information

Ranking Information over time
? how does this line up with time of match
* Probably just for production-ready apps, not available for now


Match History


Match information
Columns?

* Match ID
* puuid
* placing
* level
* Comp
* Chosen - style
* Units and Items
* gold_left
* last_round

* players_eliminated
* time_eliminated
* total_damage_to_players



In [ ]:
# codify last round into stage-round format
# units ordered by tier and number of items
    # codify items based on id
    # how to determine chosen? chosen tag in 'units'!
# codify traits into compositions? 
    # this person is going sharpshooters because.... traits + items on certain units


In [39]:
# Create table 
# Insert Values
# Repeatedly insert values

https://www.tutorialspoint.com/sqlalchemy/sqlalchemy_core_creating_table.htm
    https://leportella.com/sqlalchemy-tutorial/


SyntaxError: invalid syntax (<ipython-input-39-cdeddc0e9e93>, line 5)